# Indicateurs de valeur ajoutée des lycées d'enseignement général et technologique

# csv des labels numériques des lycées

## Import data  from api

In [81]:
#importing necessary packages
import pandas as pd
import requests
import json

# get data 
#creating the url
url = 'https://data.occitanie.education.gouv.fr/api/records/1.0/search/?dataset=fr-en-occitanie-label-numerique-lycee&q=&rows=10000&facet=annee&facet=rne&facet=departement&facet=label'
#making the request
response = requests.get(url)
#converting the response to json
data = response.json()
#appending the data to the list

#creating an empty list to store the records
records = []

#looping through the records
for record in data['records']:
    #storing the records in the list
    records.append(record['fields'])

#creating a dataframe from the json
df = pd.DataFrame(records)

## Transforming data of df

In [82]:
#transform the label to numeric
df["label"] = pd.to_numeric(df["label"])
df["annee"] = pd.to_numeric(df["annee"])

#sort annee by ascending order
df.sort_values(by="annee",inplace=True)

#create two new columns for longitude and latitude
df['latitude'] = df['position'].apply(lambda x: float(x[0]))
df['longitude'] = df['position'].apply(lambda x: float(x[1]))

# csv des résultats des lycées d'enseignement Général et technologique

## import data from csv

In [83]:
df2 = pd.read_csv("../data/lycee/csv/fr-en-indicateurs-de-resultat-des-lycees-denseignement-general-et-technologique.csv", sep=";")

/tmp/ipykernel_28674/3805400727.py:1: DtypeWarning:

Columns (47,48,49,51,52,53,55,56,57,58,59,71,72,73,74,75,76,77,78,79,80,81,93,95,98,100,111,113,115,126,129,130,131,134,136) have mixed types. Specify dtype option on import or set low_memory=False.



## Nettoyage

In [84]:
# nettoyage
# filtrer les données sur occitanie
df2 = df2.query("Region == 'OCCITANIE'")

## Transform

In [85]:
# transformation

#RENOMMAGE
df2.rename(columns={
    "Annee" : "annee",
    "Taux de reussite - Toutes series" : "taux_reussite_toutes_series",
    "Valeur ajoutee du taux de reussite - Toutes series" : "va_taux_reussite_toutes_series",
    "Taux de reussite attendu france - Toutes series" : "taux_reussite_attendu_toutes_series",
    "Departement" : "departement"
},inplace=True)


#transform the annee to numeric
df2["annee"] = pd.to_numeric(df2["annee"])
#sort annee by ascending order
df2.sort_values(by="annee",inplace=True)


# transform le taux brut en numerique
df2["taux_reussite_toutes_series"] = pd.to_numeric(df2["taux_reussite_toutes_series"])


# Operations sur les deux csv (merge)
 - csv labels numériques lycee
 - csv résultats scolaires des lycee professionnels

In [86]:
# merge 2 dataframes on the uri (id de l'etablissement scolaire)
df_result = pd.merge(df, df2, left_on='rne', right_on='UAI', how="inner")

In [87]:
# merge 2 dataframes but keep all the lycee that does not have label 
df_result_all = pd.merge(df,df2, left_on='rne', right_on='UAI', how="right")

## Nettoyage df result (resultat des lycées d'enseignement générales et technologiques numériques)

In [88]:
#nettoyage (supression) des colonnes ou toutes les valeures sont nulles
df_result.dropna(axis=1,how='all',inplace=True)

#nettoyage (supression) des lignes ou toutes les valeures sont nulles
df_result.dropna(axis=0,how='all',inplace=True)

# L'index 1393 a une valeure ajoutée de réusiite totale = "ND"
# par contre ce lycee a un taux_reussite_toutes_series = 84
# j'ai donc décidé de rempace le "ND" par 0 (neutre) pour ce lycee et pour tous les lycee qui ont
# une valeure ajoutée de réussite totale = "ND" (non définir)
import re
reg_ex1 = r"ND"
reg_ex2 = r"\."
aNegliger = re.compile(f"{reg_ex1}|{reg_ex2}",re.I)
subst = "0"
def apply_reg(str_):
    '''Fonction pour remplacer les "ND" par 0 tout court dans une colonne
        - paramètres : 
            - str_ : la chaine de caractère dans laquelle la fonction va chercher la pattern à nettoyé
        - Return la chaine de caractère nettoyé '''
    if pd.notna(str_):
        return re.sub(aNegliger, subst, str(str_))
    else:
        return str_
    
df_result['va_taux_reussite_toutes_series'] = df_result['va_taux_reussite_toutes_series'].apply(apply_reg)

## Nettoyage df result all (resultat de tous les lycées d'enseignement générales et technologiques )

In [89]:
#nettoyage (supression) des colonnes ou toutes les valeures sont nulles
df_result_all.dropna(axis=1,how='all',inplace=True)

#nettoyage (supression) des lignes ou toutes les valeures sont nulles
df_result_all.dropna(axis=0,how='all',inplace=True)

# L'index 1393 a une valeure ajoutée de réusiite totale = "ND"
# par contre ce lycee a un taux_reussite_toutes_series = 84
# j'ai donc décidé de rempace le "ND" par 0 (neutre) pour ce lycee et pour tous les lycee qui ont
# une valeure ajoutée de réussite totale = "ND" (non définir)
df_result_all['va_taux_reussite_toutes_series'] = df_result_all['va_taux_reussite_toutes_series'].apply(apply_reg)

## Transform df qui contient les resultat des lycées labelisés seulement (df_result)

In [90]:
# transformer les dates en numériques pour la prochaine opération
df_result["annee_x"] = pd.to_numeric(df_result["annee_x"])
df_result["annee_y"] = pd.to_numeric(df_result["annee_y"])

# ajouter une colonne qui contient boolean (resultat après obtention label ou pas)
# True si oui, false sinon
# les resultats des lycee après l'obtention de leurs labels 
# (annee_x pour obtention label, annee_y pour passage examens de baccalauréat)
df_result["resultat_apres_label"] = (df_result["annee_y"] >= df_result["annee_x"])

# transformer la valeur ajoutée de réussites totale en numérique
df_result["va_taux_reussite_toutes_series"] = pd.to_numeric(df_result["va_taux_reussite_toutes_series"])

# transorm taux_reussite_attendu_toutes_series to numeric
df_result["taux_reussite_attendu_toutes_series"] = pd.to_numeric(df_result["taux_reussite_attendu_toutes_series"])


## Transform df qui contient les résultats de tous les lycées inclus sont qui sont labelisés (df_result_all)

In [91]:
# transformer les dates en numériques pour la prochaine opération
# transformer les dates en numériques pour la prochaine opération
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])

# Creer une colonne pour dire si le lycee est labelisé : True/False
df_result_all["label_true"] = (pd.notna(df_result_all["rne"]))

# ajouter une colonne qui contient boolean (resultat après obtention label ou pas)
# True si oui, false sinon
# les resultats des lycee après l'obtention de leurs labels 
# (annee_x pour obtention label, annee_y pour passage examens de baccalauréat)
df_result_all["resultat_apres_label"] = (df_result_all["annee_y"] >= df_result_all["annee_x"]) & (df_result_all["label_true"] == True)

# remplacer tous les labels à 0 where examen passé avant 2017
df_result_all.loc[df_result_all["resultat_apres_label"] == False, "label"] = 0

# transformer la valeur ajoutée de réussites totale en numérique
df_result_all["va_taux_reussite_toutes_series"] = pd.to_numeric(df_result_all["va_taux_reussite_toutes_series"])

# transorm taux_reussite_attendu_toutes_series to numeric
df_result_all["taux_reussite_attendu_toutes_series"] = pd.to_numeric(df_result_all["taux_reussite_attendu_toutes_series"])

## Infos

In [92]:
df_result.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4214 entries, 0 to 4213
Columns: 147 entries, label to resultat_apres_label
dtypes: bool(1), float64(70), int64(7), object(69)
memory usage: 4.7+ MB


# Transform for visualisations

In [93]:
# re transform annee to str so it can be a discrete value for visualisations (discrete value)
df_result["annee_x"] = df_result["annee_x"].apply(str)
df_result["annee_y"] = df_result["annee_y"].apply(str)

df_result_all["annee_x"] = df_result_all["annee_x"].apply(str)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

# Visualisation 

In [94]:
# Import necessary libraries
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import folium # for maps
import plotly.graph_objects as go

## Analyse général

In [95]:
# La répartition des Ecole, lycce et collège en france

nbre_lycee_professionnel = df_result_all['UAI'].nunique()
nbre_lycee_professionel_labelise = df_result_all['rne'].nunique()
nbre_lycee_professionnel_non_labelise = nbre_lycee_professionnel - nbre_lycee_professionel_labelise
values = [nbre_lycee_professionnel_non_labelise,nbre_lycee_professionel_labelise]
labels = ["nombre de lycées d'enseignement générales et technologiques  non labelisés pour lesquelles on connait le resultat", "nombre de lycées d'enseignement générales et technologiques  labelisés pour lesquelles on connait le resultat"]

fig = go.Figure(data=[go.Pie(labels=labels, values=values, title = "La proportions des Lycées labelisés parmis les professionels")])
fig.show()

In [96]:
# La variation du nombre des lycées labelisés selon les années
df_proportion_lycee_labelise_annee = df_result.groupby("annee_x")["rne"].nunique()
df_proportion_lycee_labelise_annee = df_proportion_lycee_labelise_annee.reset_index()

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_labelise_annee, x="annee_x", y="rne",
                   color="annee_x",
                      labels={"UAI" : "nombre de lycee labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées labelisés selon les années")
fig.show()

**le nombre de lycées d'enseignement générales et technologiques  labelisés a augmente de 57,31 % entre 2017 et 2021**

In [97]:
# La variation du nombre des lycées non labelisés selon les années
df_proportion_lycee_non_labelise_annee = df_result_all.query("label_true == False").groupby("annee_y")["UAI"].nunique()
df_proportion_lycee_non_labelise_annee = df_proportion_lycee_non_labelise_annee.reset_index()

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_non_labelise_annee, x="annee_y", y="UAI",
                   color="annee_y",
                      labels={"UAI" : "nombre de lycee non labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées non labelisés selon les années")
fig.show()

**Le nombre de lycées d'enseignement générales et technologiques  non labelisés a augmenté de 7.4% entre 2012 et 2021**

In [98]:
# La variation du nombre des lycées d'enseignement générales et technologiques  (labelisé ou non) selon les années
df2["annee"] = df2["annee"].apply(str)
df_proportion_lycee_tout_annee = df2.groupby("annee")["UAI"].nunique()
df_proportion_lycee_tout_annee = df_proportion_lycee_tout_annee.reset_index()
df_proportion_lycee_tout_annee

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_tout_annee, x="annee", y="UAI",
                   color="annee",
                      labels={"UAI" : "nombre de lycee non labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées d'enseignement générales et technologiques  (labelisés et non labelisés) selon les années")
fig.show()

**Le nombre des lycées d'enseignement générales et technologiques  (labelisés et non labelisé) a augmenté de 5.17% entre 2012 et 2021**

### Conclusion

**Au fil des années, les lycées d'enseignement générales et technologiques non labelisés et labelisés augmentent**

## Analyse du taux brut de réussite des élèves dans les lycées

**Taux de réussite constaté**

- Le taux de réussite au baccalauréat est la proportion, parmi les élèves présents à l’examen, de ceux qui ont obtenu le diplôme
- Le graphique ci-dessous montre que le moyenne du taux de réussite est presque similaire selon que l'école
    a un abel 1 ou 3.
- Il est donc intéréssant d'aller voir qu'elle étaient les moyennes de taux de réussite de ces écoles avant
    obtention de leurs labels numérique !

In [99]:
# transform label to numeric
df_result["label"] = pd.to_numeric(df_result["label"])
#sort label by ascending order
df_result.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result["label"] = df_result["label"].apply(str)

#plotting a histogram
fig = px.histogram(df_result[df_result["resultat_apres_label"] == True], x="label", y="taux_reussite_toutes_series", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux bruts de réussites des lycee après obtention de leurs labels (tous secteurs) selon les labels")
fig.show()

### A NOTER LABEL 0 = PAS DE LABEL

In [100]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram
fig = px.histogram(df_result_all, x="label", y="taux_reussite_toutes_series", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux bruts de réussites des lycee sans (label 0) et avec des labels (tous secteurs) selon les labels")
fig.show()

**Comparaison de la moyenne du taux de réussite constaté avant et après obtention des labels numériques**

- Le graphique ci-dessous montre une amélioration des taux de réussite des écoles après obtention de leurs labels
    numérique !
- IL est donc intéréssant d'aller chercher pourquoi ? est ce que l'école a apporté plus de valeur pour les 
    élèves grace au numérique ?

In [101]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="taux_reussite_toutes_series", nbins=10,
                       histfunc="avg", color="departement_y",
                       facet_row="resultat_apres_label",
                      labels={"taux_reussite_toutes_series" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites (tous secteurs) selon les départements - avant et après obtention labels")
fig.show()

### La moyenne des taux bruts de réussites (tous secteurs) avant et après obtention labels

In [102]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="taux_reussite_toutes_series", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_reussite_toutes_series" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites (tous secteurs) avant et après obtention labels")
fig.show()

In [103]:
#plotting a histogram 
fig = px.histogram(df_result, x="rne", y="taux_reussite_toutes_series", nbins=10, histfunc="avg", color="departement_y", facet_row="resultat_apres_label",
                  labels={"taux_reussite_toutes_series" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites de chaque lycée (tous secteurs) avant et après obtention labels")
fig.show()

**Pourquoi certains lycées n'apparaissent pas dans le resultat après labels malgré qu'ils ont des labels ?**
- simplement parce ces lycées n'ont pas eu de passages d'examens après obtentions de labels (peut etre étrange mais 
    voici les données suivantes comme exemple pour l'école 0480009Z

In [106]:
df_result[df_result['rne'] == "0480009Z"][["label","annee_x","annee_y","UAI","resultat_apres_label"]]

label annee_x annee_y       UAI  resultat_apres_label
1276     1    2017    2012  0480009Z                 False
1277     1    2017    2013  0480009Z                 False
1279     1    2017    2015  0480009Z                 False
1280     1    2017    2016  0480009Z                 False
1281     1    2017    2017  0480009Z                  True
1282     1    2017    2018  0480009Z                  True
1283     1    2017    2019  0480009Z                  True
1284     1    2017    2020  0480009Z                  True
1278     1    2017    2014  0480009Z                 False
1285     1    2017    2021  0480009Z                  True
1286     1    2018    2012  0480009Z                 False
1288     1    2018    2014  0480009Z                 False
1306     1    2021    2012  0480009Z                 False
1307     1    2021    2013  0480009Z                 False
1308     1    2021    2014  0480009Z                 False
1309     1    2021    2015  0480009Z                 False
1310     1    2021    2016  0480009Z                 False
1311     1    2021    2017  0480009Z                 False
1305     1    2019    2021  0480009Z                  True
1304     1    2019    2020  0480009Z                  True
1289     1    2018    2015  0480009Z                 False
1290     1    2018    2016  0480009Z                 False
1291     1    2018    2017  0480009Z                 False
1292     1    2018    2018  0480009Z                  True
1293     1    2018    2019  0480009Z                  True
1294     1    2018    2020  0480009Z                  True
1295     1    2018    2021  0480009Z                  True
1296     1    2019    2012  0480009Z                 False
1297     1    2019    2013  0480009Z                 False
1298     1    2019    2014  0480009Z                 False
1299     1    2019    2015  0480009Z                 False
1300     1    2019    2016  0480009Z                 False
1301     1    2019    2017  0480009Z                 False
1302     1    2019    2018  0480009Z                 False
1303     1    2019    2019  0480009Z                  True
1287     1    2018    2013  0480009Z                 False
1312     1    2021    2018  0480009Z                 False
1313     1    2021    2019  0480009Z                 False
1315     1    2021    2021  0480009Z                  True
1314     1    2021    2020  0480009Z                 False

### On va voir la différence des résultats entre les lycées labelisés et ceux qui ne le sont pas

In [107]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="taux_reussite_toutes_series", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_reussite_toutes_series" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites sans et avec labels")
fig.show()

In [108]:
#plotting a bocplot 
fig = px.box(df_result_all, x="resultat_apres_label", y="taux_reussite_toutes_series",
             color="resultat_apres_label",
            labels={"taux_reussite_toutes_series" : "taux brut de réussite"})
fig.update_layout(title_text="La variance des taux bruts de réussites sans et avec labels")
fig.show()

In [109]:
# transform label to numeric
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])
#sort label by ascending order
df_result_all.sort_values(by="annee_y",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

#plotting a bocplot 
fig = px.box(df_result_all, x="annee_y", y="taux_reussite_toutes_series",
             color="resultat_apres_label",
            labels={"taux_reussite_toutes_series" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites sans et avec labels par année")
fig.show()

**On constate que les lycées d'enseignement générales et technologiques  non labelisés ont un meilleur résultat que ceux labelisés (toutes années confondues)**
 - On se demande pourquoi ?
 - On sait que parmis les lycées d'enseignement générales et technologiques , 32,5% ne sont pas labelisés, et 67,5% sont labelisés.
 - Alors nous souhaitons répondre à la question suivante : y'a t'il un effet de la labélisation sur le taux de réussite des lycées d'enseignement générales et technologiques  ?
 - Pour cela on pose les hypothèses suivantes : 
     - H0 : La labélisation d'un lycee professionel n'a pas d'effet sur son taux brut de réussite tous secteurs
     - H1 : La labélisation d'un lycee professionel a un effet sur son taux brut de réussite tous secteurs

### Covid
**Nous constatons un pic de taux de réussite des lycées d'enseignement générales et technologiques  en 2020, puis une diminution de ce taux en 2021**

## Analyse de la valeur ajoutée de réussite 
- la valeur ajoutée de l’établissement est la différence entre le taux constaté de l’établissement et le taux attendu. 

    **Valeur ajoutée = taux constaté – taux attendu**
    

- Le graphique ci-dessous montre une moyenne de valeur ajoutée de label 3 plus petite que label 1.
    C'est étonnant, mais est-ce que ça veut dire que les écoles ayant un label 3 ont contribué moins
    à la réussite des élèves ? Pas nécessairement.
- En effet, peut etre que les écoles ayant un label 3, ont un taux de réussite attendu beaucoup plus elevé 
    que les écoles avec un label plus faible. De ce fait, l'augmentation du taux de réussite attendu 
    peut diminuer la valeur ajoutée de l'école.

In [110]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram 
fig = px.histogram(df_result_all, x="label", y="va_taux_reussite_toutes_series", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des valeurs ajoutées de réussites (tous secteurs) selon les labels")
fig.show()

**Comparaison des valeurs ajoutées des écoles avant et après obtention des labels numériques**

- le graphique ci-dessous montre une véritables amélioration des valeurs ajoutée des écoles après obtention de labels. Surtout pour le département de LOZERE pour lequel la valeur ajoutée est passée du **-** à **+** !

In [111]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="va_taux_reussite_toutes_series", nbins=10, histfunc="avg", color="departement_y", facet_row="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites (tous secteurs) selon les départements avant et après obtention labels")
fig.show()

In [112]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="va_taux_reussite_toutes_series", nbins=10, histfunc="avg", color="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites (tous secteurs) avant et après obtention labels")
fig.show()

### Comparaison de la moyenne des valeurs ajoutés de réussites (toutes séries) des lycées d'enseignement générales et technologiques sans et avec labels

In [114]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="va_taux_reussite_toutes_series", nbins=10, histfunc="avg", color="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites (tous secteurs) sans et avec labels")
fig.show()

In [115]:
#plotting a bocplot 
fig = px.box(df_result_all, x="resultat_apres_label", y="va_taux_reussite_toutes_series",
             color="resultat_apres_label",
            labels={"va_taux_reussite_toutes_series" : "taux de valeur ajoutée total secteurs"})
fig.update_layout(title_text="La variance des taux bruts de réussites sans et avec labels")
fig.show()

In [116]:
# transform label to numeric
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])
#sort label by ascending order
df_result_all.sort_values(by="annee_y",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

#plotting a bocplot 
fig = px.box(df_result_all, x="annee_y", y="va_taux_reussite_toutes_series",
             color="resultat_apres_label",
            labels={"va_taux_reussite_toutes_series" : "taux de valeur ajoutée total secteurs"})
fig.update_layout(title_text="La variance des taux bruts de réussites sans et avec labels par année")
fig.show()

## Analyse du taux de réussite attendu en france (toutes séries)

In [118]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram 
fig = px.histogram(df_result_all, x="label", y="taux_reussite_attendu_toutes_series", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) selon les labels")
fig.show()

### Comparaison du taux de réussite des élèces aux lycées d'enseignement générales et technologiques  attendu en france total secteurs avant et  après obtention des labels

In [119]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="taux_reussite_attendu_toutes_series", nbins=10,
                       histfunc="avg", color="departement_y",
                       facet_row="resultat_apres_label",
                      labels={"taux_reussite_attendu_toutes_series" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) selon les départements - avant et après obtention labels")
fig.show()

In [120]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="taux_reussite_attendu_toutes_series", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_reussite_attendu_toutes_series" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) avant et après obtention labels")
fig.show()

### Comparaison du taux de réussite des élèves aux lycées d'enseignement générales et technologiques  attendu en france total secteurs sans et avec labels

In [122]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="taux_reussite_attendu_toutes_series", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_reussite_attendu_toutes_series" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) sans et avec labels")
fig.show()

## Analyse temporelles

In [124]:
# transform label to numeric
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])
#sort label by ascending order
df_result_all.sort_values(by="annee_y",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

fig = px.scatter(df_result_all,
                 x = "annee_y",
                 y = "taux_reussite_toutes_series",
                 color = "UAI",
                 hover_name="taux_reussite_toutes_series",
             hover_data=["label"],
             title = "Le taux de réussite des lycées d'enseignement générales et technologiques  non labeisés en 2012 en fonction des années")

plt.tight_layout()
fig.show()

<Figure size 432x288 with 0 Axes>

# ANOVA 

## Effet de la labélisation sur le taux brut de réussite des lycées d'enseignement générales et technologiques  tous secteurs

In [125]:
import statsmodels.api as sa
import statsmodels.formula.api as sfa
import scikit_posthocs as sp
from statsmodels.stats.multicomp import pairwise_tukeyhsd
import scipy.stats as stats

### Résultat de l'anova

In [126]:
lm = sfa.ols('taux_reussite_toutes_series ~ C(label)', data=df_result_all).fit()
anova = sa.stats.anova_lm(lm)
anova

df         sum_sq      mean_sq          F        PR(>F)
C(label)     3.0    5745.308058  1915.102686  82.611728  4.199653e-52
Residual  4775.0  110693.912281    23.181971        NaN           NaN

### Analyse de l'anova

**P_value < alpha (0,05), donc on rejette H0 et on conclut d'une manière significative un effet du label numérique sur le taux brut de réussite des lycées d'enseignement générales et technologiques  tous secteurs**

### Test de Tukey
 - permet de préciser quelles modalités de la variable qualitative label a provoqué ce rejet

In [127]:
# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df_result_all['taux_reussite_toutes_series'],
                          groups=df_result_all['label'],
                          alpha=0.05)

#display results
print(tukey)

Multiple Comparison of Means - Tukey HSD, FWER=0.05
group1 group2 meandiff p-adj   lower  upper  reject
---------------------------------------------------
   0.0    1.0   2.6784    0.0  2.2044 3.1523   True
   0.0    2.0   2.0858    0.0  1.3578 2.8137   True
   0.0    3.0   1.6905 0.0006  0.5685 2.8126   True
   1.0    2.0  -0.5926 0.2433 -1.4092  0.224  False
   1.0    3.0  -0.9879  0.138 -2.1693 0.1936  False
   2.0    3.0  -0.3952 0.8641 -1.6995 0.9091  False
---------------------------------------------------


### Analyse de test de tukey 
**Le test de tukey est utilisé pour comparer les moyennes de plusieurs groupes. Le test est utilisé pour déterminer s'il existe des différences significatives entre les moyennes de différents groupes.
L'output montre les résultats du test pour chaque comparaison à paires de groupes. Les colonnes de l'output incluent:**
- group1 et group2: les groupes étant comparés
- meandiff: la différence des moyennes entre les deux groupes
- p-adj: la valeur p ajustée pour la comparaison
- lower et upper: les limites inférieure et supérieure de l'intervalle de confiance de 95% pour la différence des moyennes
- reject: si oui ou non l'hypothèse nulle (que les moyennes sont égales) peut être rejetée en fonction de la valeur p et du niveau alpha choisi (0,05 dans ce cas)

**Ce test compare les moyennes de quatre groupes: 0.0, 1.0, 2.0 et 3.0.**
- Pour le groupe 0.0 et 1.0, la valeur p-adj est de 0.0, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05.
- Pour le groupe 0.0 et 2.0, la valeur p-adj est de 0.0, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05
- Pour le groupe 0.0 et 3.0, la valeur p-adj est de 0.0, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05

### Shapiro test : Tester l'hypothèse de normalité
 - H0 : Les échatillons sont gaussiens

In [128]:
# Split the data
x = df_result_all.groupby('label')['taux_reussite_toutes_series'].apply(list)

In [129]:
# Perform Shapiro-Wilk test
stat, p = stats.shapiro(x[0])
print("Shapiro-Wilk test: statistic=%f, p-value=%f" % (stat, p))
if p > 0.05:
    print("The data is likely normal")
else:
    print("The data is likely not normal")

Shapiro-Wilk test: statistic=0.953409, p-value=0.000000
The data is likely not normal


**p value < 0.05 donc on rejette H0 et on conclut que les échantillons ne sont plutot pas gaussiens**

### Levene's test : Tester l'hypothèse d'homoscédasticité
- H0 : Les variances sont égales

**L'hyphothèse de normalité n'est pas validé, donc on réalise un test de Levene pour tester l'hypothèse d'homoscédasticité**

In [130]:
# Perform Levene's test
stat, p = stats.levene(x[0], x[1], x[2], x[3])
print("Levene's test: statistic=%.3f, p-value=%.3f" % (stat, p))
if p > 0.05:
    print("The variances of the samples are likely similar")
else:
    print("The variances of the samples are likely different")

Levene's test: statistic=13.646, p-value=0.000
The variances of the samples are likely different


**p value < 0,05 donc on rejette H0 et on conclut que les variances des labels ne sont plutot pas égales**

## Effet de la labélisation sur le taux brut de réussite des lycées d'enseignement générales et technologiques  tous secteurs
### Résultat de l'anova

In [131]:
lm = sfa.ols('va_taux_reussite_toutes_series ~ C(label)', data=df_result_all).fit()
anova = sa.stats.anova_lm(lm)
anova

df        sum_sq    mean_sq         F    PR(>F)
C(label)     3.0     99.515442  33.171814  2.931535  0.032255
Residual  4775.0  54031.557167  11.315509       NaN       NaN

### Analyse de l'anova

**P_value < alpha (0,05), donc on rejette H0 et on conclut d'une manière significative un effet du label numérique sur la valeur ajoutée de réussite des lycées d'enseignement générales et technologiques  tous secteurs**

### Test de Tukey

In [132]:
# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df_result_all['va_taux_reussite_toutes_series'],
                          groups=df_result_all['label'],
                          alpha=0.05)

#display results
print(tukey)

Multiple Comparison of Means - Tukey HSD, FWER=0.05 
group1 group2 meandiff p-adj   lower   upper  reject
----------------------------------------------------
   0.0    1.0   0.2387 0.2488 -0.0924  0.5698  False
   0.0    2.0   0.1737 0.8165 -0.3349  0.6822  False
   0.0    3.0    -0.62 0.1762 -1.4039  0.1639  False
   1.0    2.0  -0.0651 0.9912 -0.6356  0.5054  False
   1.0    3.0  -0.8587 0.0378 -1.6842 -0.0333   True
   2.0    3.0  -0.7937 0.1132 -1.7049  0.1176  False
----------------------------------------------------


### Analyse de test de tukey 

**Ce test compare les moyennes de quatre groupes: 0.0, 1.0, 2.0 et 3.0.**
- Pour le groupe 1.0 et 3.0, la valeur p-adj est de 0.0378, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05

### Shapiro test : Tester l'hypothèse de normalité
 - H0 : Les échatillons sont gaussiens

In [133]:
# Split the data
x = df_result_all.groupby('label')['va_taux_reussite_toutes_series'].apply(list)

In [134]:
# Perform Shapiro-Wilk test
stat, p = stats.shapiro(x[0])
print("Shapiro-Wilk test: statistic=%f, p-value=%f" % (stat, p))
if p > 0.05:
    print("The data is likely normal")
else:
    print("The data is likely not normal")

Shapiro-Wilk test: statistic=0.975870, p-value=0.000000
The data is likely not normal


### Levene's test : Tester l'hypothèse d'homoscédasticité
- H0 : Les variances sont égales

In [135]:
# Perform Levene's test
stat, p = stats.levene(x[0], x[1], x[2], x[3])
print("Levene's test: statistic=%.3f, p-value=%.3f" % (stat, p))
if p > 0.05:
    print("The variances of the samples are likely similar")
else:
    print("The variances of the samples are likely different")

Levene's test: statistic=72.948, p-value=0.000
The variances of the samples are likely different
